In [1]:
from cassandra.auth import PlainTextAuthProvider
from cassandra.cluster import Cluster
import os
import os.path
import spacy

%run ./REST.ipynb
%run ./GamePatterns.ipynb
%run ./nlpProcessedGame.ipynb

%run ./MatcherLocalizer.ipynb
%run ./RegexLocalizer.ipynb


In [2]:
client = empamos_rest_client()
p = client.get_patterns_name_dictionary()

pattern_names = client.get_patterns_name_dictionary()
nlp = spacy.load("de")

In [3]:
class metrics:
    
    def recall(self):
        if (self.tp == 0):
            return 0
        return self.tp / ( self.tp + self.fn)
    
    def precision(self):
        if (self.tp == 0):
            return 0
        return self.tp / (self.tp + self.fp)
    
    def accuracy(self):
        if (self.tp+ self.tn == 0):
            return 0
        return (self.tp + self.tn) / (self.tp + self.tn + self.fp + self.fn)
    
    def F1(self):
        if (self.tp == 0):
            return 0
        return  2 * self.tp / (2*self.tp + self.fp + self.fn)

In [4]:
pattern_terms_file_name = "pattern_terms.json"
pattern_expressions_file_name = "pattern_expressions.json"

validator_directory = "Validator_sentences"

In [5]:
localizers = []
localizers_names = []  #for debugging

In [6]:
patloc = matcher_localizer()
myFile = open(pattern_terms_file_name, "r")
pattern_terms = myFile.read()
pattern_terms = json.loads(pattern_terms)
patloc.init_matcher(nlp,pattern_terms)
localizers.append(patloc)
localizers_names.append("Matcher Lower")


In [7]:
lemloc = matcher_localizer()
myFile = open(pattern_terms_file_name, "r")
pattern_terms = myFile.read()
pattern_terms = json.loads(pattern_terms)
lemloc.init_matcher_lemma(nlp,pattern_terms)
localizers.append(lemloc)
localizers_names.append("Matcher Lemma")


In [8]:
regloc = regex_localizer()
myFile = open(pattern_expressions_file_name, "r")
pattern_expressions = myFile.read()
pattern_expressions = json.loads(pattern_expressions)
regloc.init(pattern_expressions,False)
localizers.append(regloc)
localizers_names.append("Regex ohne Lemma")


In [9]:
regloc = regex_localizer()
myFile = open(pattern_expressions_file_name, "r")
pattern_expressions = myFile.read()
pattern_expressions = json.loads(pattern_expressions)
regloc.init(pattern_expressions,True)
localizers.append(regloc)
localizers_names.append("Regex mit Lemma")


In [10]:
def validate(pattern):  
    pos_file_name = validator_directory+"/"+str(pattern)+"-pos.txt"
    neg_file_name = validator_directory+"/"+str(pattern)+"-neg.txt"
    with open(pos_file_name,"r") as f: 
        pos_sentences = f.readlines()
        pos_sentences = [x.strip() for x in pos_sentences]
        pos_sentences = " ".join(pos_sentences)

    useNeg = os.path.isfile(neg_file_name) 
    
    if(useNeg):
        with open(neg_file_name,"r") as f: 
            neg_sentences = f.readlines()
            neg_sentences = [x.strip() for x in neg_sentences]
            neg_sentences = " ".join(neg_sentences)
    
    
    processed_game_pos = nlp_processed_game()
    processed_game_pos.set_ID(pattern)
    processed_game_pos.set_spacy_doc(nlp(pos_sentences))
    if(useNeg):
        processed_game_neg = nlp_processed_game()
        processed_game_neg.set_ID(pattern)
        processed_game_neg.set_spacy_doc(nlp(neg_sentences))
    cnt = 0
    metrics_list = []
    print("Pattern "+ str(pattern) + ":" + pattern_names[pattern])

    for localizer in localizers:
        print("")
        metric = metrics()
        metrics_list.append(metric)
        metric.hasNeg = useNeg
        if cnt < len(localizers_names):
            print(localizers_names[cnt])
            metric.localizer_name = localizers_names[cnt]
        cnt += 1

        gp = localizer.read_nlp_processed_game_to_game_patterns(processed_game_pos )   

        try:
            tp = len(gp.patterns[pattern])
        except:
            print("Pattern not found!")
            tp = 0
            
        fn = gp.get_sentence_count() - tp

        metric.tp = tp
        metric.fn = fn

        print("Tp: " + str(metric.tp))
        print("Fn: " + str(metric.fn))

        if(useNeg):
            gp2 = localizer.read_nlp_processed_game_to_game_patterns(processed_game_neg )

            try:
                fp = len(gp2.patterns[pattern])
            except:
                fp = 0
            tn = gp2.get_sentence_count() - fp    
            metric.fp = fp
            metric.tn = tn


            print("Fp: " + str(metric.fp))
            print("Tn: " + str(metric.tn))

        print("Recall: " + str(metric.recall()))
        if(useNeg):
            print("Precision: " + str(metric.precision()))
            print("Accuracy: " + str(metric.accuracy()))
            print("F1: " + str(metric.F1()))

        gp.print_sentences_with_patterns(pattern_names)
        if(useNeg):
            gp2.print_sentences_with_patterns(pattern_names)
        #print(gp.patterns)
        print("")
        #gp.print_sentences_with_patterns(pattern_names)
    return metrics_list

In [11]:
all_metrics = {}
for pattern in pattern_names:
    all_metrics[pattern] = validate(pattern)



Pattern 1292:Zufall

Matcher Lower
Pattern not found!
Tp: 0
Fn: 161
Fp: 0
Tn: 154
Recall: 0
Precision: 0
Accuracy: 0.4888888888888889
F1: 0
0: Die 98 Zahlenkarten werden gründlich gemischt.; []
1: Sie werden gemischt und verdeckt (=Hasenseite nach oben) als Stapel neben den Spielplan gelegt).; [3173: Gemeinsames Spielfeld, 8528: Siegpunkte, ]
2: Alle Steine kommen in den Beutel und werden gut gemischt.; [73230: Symmetrische Startbedingung, ]
3: Dazu legt er die Steine, die er eintauschen will, beiseite und zieht anschließend die entsprechende Anzahl an „Austausch-Steinen“ blind aus dem Beutel nach.; [3173: Gemeinsames Spielfeld, ]
4: Wenn der Beutel leer ist, können die Spieler nach dem Legen der Steine keine neuen Steine mehr nachziehen.; []
5: Nehmt 25 zufällige Wortkarten und legt sie in einem 5-mal-5-Raster auf den Tisch aus.; [3173: Gemeinsames Spielfeld, ]
6: Beim Mischen sollte man gelegentlich die Hälfte der Karten auf die andere Seite drehen.; [8528: Siegpunkte, ]
7: Dadurch d

Fp: 0
Tn: 154
Recall: 0
Precision: 0
Accuracy: 0.4888888888888889
F1: 0
0: Die 98 Zahlenkarten werden gründlich gemischt.; [3173: Gemeinsames Spielfeld, ]
1: Sie werden gemischt und verdeckt (=Hasenseite nach oben) als Stapel neben den Spielplan gelegt).; [3173: Gemeinsames Spielfeld, 8528: Siegpunkte, ]
2: Alle Steine kommen in den Beutel und werden gut gemischt.; [3173: Gemeinsames Spielfeld, 73230: Symmetrische Startbedingung, ]
3: Dazu legt er die Steine, die er eintauschen will, beiseite und zieht anschließend die entsprechende Anzahl an „Austausch-Steinen“ blind aus dem Beutel nach.; [3173: Gemeinsames Spielfeld, ]
4: Wenn der Beutel leer ist, können die Spieler nach dem Legen der Steine keine neuen Steine mehr nachziehen.; [3173: Gemeinsames Spielfeld, ]
5: Nehmt 25 zufällige Wortkarten und legt sie in einem 5-mal-5-Raster auf den Tisch aus.; [3173: Gemeinsames Spielfeld, ]
6: Beim Mischen sollte man gelegentlich die Hälfte der Karten auf die andere Seite drehen.; [3173: Gemeins

Tp: 152
Fn: 9
Fp: 17
Tn: 137
Recall: 0.9440993788819876
Precision: 0.8994082840236687
Accuracy: 0.9174603174603174
F1: 0.9212121212121213
0: Die 98 Zahlenkarten werden gründlich gemischt.; [1292: Zufall, ]
1: Sie werden gemischt und verdeckt (=Hasenseite nach oben) als Stapel neben den Spielplan gelegt).; [1292: Zufall, 3173: Gemeinsames Spielfeld, ]
2: Alle Steine kommen in den Beutel und werden gut gemischt.; [1292: Zufall, ]
3: Dazu legt er die Steine, die er eintauschen will, beiseite und zieht anschließend die entsprechende Anzahl an „Austausch-Steinen“ blind aus dem Beutel nach.; [1292: Zufall, ]
4: Wenn der Beutel leer ist, können die Spieler nach dem Legen der Steine keine neuen Steine mehr nachziehen.; [1292: Zufall, ]
5: Nehmt 25 zufällige Wortkarten und legt sie in einem 5-mal-5-Raster auf den Tisch aus.; [1292: Zufall, ]
6: Beim Mischen sollte man gelegentlich die Hälfte der Karten auf die andere Seite drehen.; [1292: Zufall, ]
7: Dadurch durchmischen sich die Begriffe bess

Tp: 152
Fn: 9
Fp: 15
Tn: 139
Recall: 0.9440993788819876
Precision: 0.9101796407185628
Accuracy: 0.9238095238095239
F1: 0.926829268292683
0: Die 98 Zahlenkarten werden gründlich gemischt.; [1292: Zufall, ]
1: Sie werden gemischt und verdeckt (=Hasenseite nach oben) als Stapel neben den Spielplan gelegt).; [1292: Zufall, 3173: Gemeinsames Spielfeld, ]
2: Alle Steine kommen in den Beutel und werden gut gemischt.; [1292: Zufall, ]
3: Dazu legt er die Steine, die er eintauschen will, beiseite und zieht anschließend die entsprechende Anzahl an „Austausch-Steinen“ blind aus dem Beutel nach.; [1292: Zufall, ]
4: Wenn der Beutel leer ist, können die Spieler nach dem Legen der Steine keine neuen Steine mehr nachziehen.; [1292: Zufall, ]
5: Nehmt 25 zufällige Wortkarten und legt sie in einem 5-mal-5-Raster auf den Tisch aus.; [1292: Zufall, ]
6: Beim Mischen sollte man gelegentlich die Hälfte der Karten auf die andere Seite drehen.; [1292: Zufall, ]
7: Dadurch durchmischen sich die Begriffe besse

Pattern 1409:Wählbarer Schwierigkeitsgrad

Matcher Lower
Pattern not found!
Tp: 0
Fn: 100
Recall: 0
0: Unterschiedliche Kombinationen der Abenteurer, die mitspielen, bieten immer wieder neue Herausforderungen und neuen Spielspaß.; []
1: Die verbotene Insel ist ein sehr variables Spiel.; []
2: Mit ihm wird der Schwierigkeitsgrad des Spiels eingestellt (in den ersten Spielen ist es ratsam, den Anzeiger auf „Anfänger“ zu stellen).; [3173: Gemeinsames Spielfeld, ]
3: Einstellen des Wasserpegels:; [3173: Gemeinsames Spielfeld, ]
4: Natürlich könnt ihr auch weniger oder mehr Karten nehmen, um kürzer oder länger zu spielen.; [8528: Siegpunkte, ]
5: Nehmt eure Spielfiguren vom Spielbrett und stellt das Katapult auf das quadratische Feld in die Mitte der Schatzinsel.; [3173: Gemeinsames Spielfeld, 8528: Siegpunkte, ]
6: Ihr könnt bei jedem Spiel eine andere Position für das Schiff wählen.; []
7: Die Zusammenstellung der 10 Karten kann von Spiel zu Spiel variieren.; [8528: Siegpunkte, ]
8: Die e

...

Pattern not found!
Tp: 0
Fn: 126
Recall: 0
0: Schafft ihr es, vier Karotten zu ernten, bevor der Hase vier Karotten aus eurem Garten stibitzt hat?; []
1: Das Spiel endet sofort, wenn ... ... der Hase die vierte Karotte stibitzt hat.; []
2: Leider habt ihr in diesem Fall alle verloren.; []
3: Ihr habt euch als erfolgreiche Gärtner erwiesen und gewinnt das Spiel gemeinsam.; []
4: Spielaufgabe; []
5: Die Spieler jagen gemeinsam den Fuchs.; []
6: Ende des Spiels; []
7: Die Spieler haben alle gemeinsam gewonnen, wenn sie die 4 Sperrfelder am Ende des Weges besetzen können, bevor der Fuchs auf seiner Bahn dort angekommen ist, also auch unterwegs einen Ausbruch des Fuchses verhindern konnten.; []
8: Der Fuchs hat gegen alle Spieler gewonnen, wenn er unterwegs oder am Schluß irgendein freies Sperrfeld erreichen kann.; []
9: Spielziel; []
10: Helft dem kleinen Drachen Kokosnuss und seinen Freunden, sich als Mumien zu verkleiden und die goldene Maske des Pharaos vor den Grabräubern zu retten!; [

Pattern 176363:Gebietsherrschaft

Matcher Lower
Pattern not found!
Tp: 0
Fn: 62
Recall: 0
0: Ziel des Spiels ist es, zuerst drei Chips einer Farbe in waagerechter, senkrechter oder diagonaler Reihe zu haben.; [3173: Gemeinsames Spielfeld, ]
1: Wer es zuerst schafft, drei seiner Chips in waagerechter, senkrechter oder diagonaler Reihe zu platzieren, durchquert den Rechen-Dschungel und gewinnt die Spielrunde.; [3173: Gemeinsames Spielfeld, 8528: Siegpunkte, ]
2: Ihre Aufgabe besteht darin, die 8 feindlichen Herrscher aus ihren Ländern zu verjagen und so viele wertvolle Gebiete wie möglich einzunehmen.; []
3: Die Spieler fallen zunächst in die feindlichen Gebiete ein, indem sie ihre Jurten auf dem Spielplan einsetzen.; [8528: Siegpunkte, ]
4: Danach können sie 2 oder mehr angrenzende Gebiete erobern.; []
5: Dazu legen sie ein passendes Eroberungsplättchen über die Jurten (dabei dürfen auch die Jurten anderer Spieler überdeckt werden).; []
6: Bonuspunkte winken den Spielern, die am Ende di

Pattern not found!
Tp: 0
Fn: 62
Recall: 0
0: Ziel des Spiels ist es, zuerst drei Chips einer Farbe in waagerechter, senkrechter oder diagonaler Reihe zu haben.; [1292: Zufall, ]
1: Wer es zuerst schafft, drei seiner Chips in waagerechter, senkrechter oder diagonaler Reihe zu platzieren, durchquert den Rechen-Dschungel und gewinnt die Spielrunde.; []
2: Ihre Aufgabe besteht darin, die 8 feindlichen Herrscher aus ihren Ländern zu verjagen und so viele wertvolle Gebiete wie möglich einzunehmen.; []
3: Die Spieler fallen zunächst in die feindlichen Gebiete ein, indem sie ihre Jurten auf dem Spielplan einsetzen.; [3173: Gemeinsames Spielfeld, ]
4: Danach können sie 2 oder mehr angrenzende Gebiete erobern.; []
5: Dazu legen sie ein passendes Eroberungsplättchen über die Jurten (dabei dürfen auch die Jurten anderer Spieler überdeckt werden).; []
6: Bonuspunkte winken den Spielern, die am Ende die größten zusammenhängenden Gebiete aufweisen können.; [8528: Siegpunkte, ]
7: Mit List und Tücke v

Pattern 182950:Täuschen

Matcher Lower
Pattern not found!
Tp: 0
Fn: 25
Recall: 0
0: Eine davon muß wahr sein.; []
1: Eine davon muß wahr sein.; []
2: Ein Täuschungsspiel, bei dem gelogen wird, daß sich die Balken biegen.; []
3: Das funktioniert natürlich nur, weil man in diesem Spiel ohne Ende hochstapeln kann.; []
4: Jeder darf; [73230: Symmetrische Startbedingung, ]
5: nach Strich und Faden lügen Jetzt kann man auch bluffen.; []
6: Dies geschieht entweder durch das Auslegen von Karten - wobei fleißig geschummelt werden darf - oder durch das Abwerfen von kompletten Tierarten.; [8528: Siegpunkte, ]
7: Hier ist es nun, das heftige Bluff-Spiel, das Nerven aus Stahl, Mut und eine scharfsinnige Strategie erfodert.; []
8: Ihr dürft alles behaupten, aber niemandem eure Karte zeigen.; []
9: Mit List und Tücke versucht jeder, ein Gebiet mit einer möglichst wertvollen Schafherde einzu- zäunen.; [73230: Symmetrische Startbedingung, ]
10: Wer am Zuge ist und glaubt, in der bestehenden Kette einen

Pattern 183168:Abstimmung

Matcher Lower
Pattern not found!
Tp: 0
Fn: 21
Recall: 0
0: Bei einer „Anschuldigung“ behauptet die Mehrheit der Spieler (Abstimmung mit einfacher Mehrheit), daß die Rolle, die ein Spieler spielt, nicht seine „wahre“ Identität ist.; [8528: Siegpunkte, ]
1: Dieser letzte Spieler ist das Opfer der Abstimmung des Dorfes.; [3173: Gemeinsames Spielfeld, ]
2: Zu Abstimmungen kann es unter verschiedenen Umständen kommen, z. B. wenn ein Spieler in die Verbannung geschickt werden soll oder eine Schicksalskarte dazu aufruft.; []
3: Diese Entscheidung müsst ihr einstimmig fällen; []
4: Wenn alle eingeladenen Spieler zustimmen; [73230: Symmetrische Startbedingung, ]
5: Nach ein paar Minuten Diskussion wird abgestimmt; []
6: Alle Spieler entscheiden gemeinsam, welches die beste Lösung ist.; [73230: Symmetrische Startbedingung, ]
7: Die Spieler können miteinander reden, verhandeln, argumentieren oder Allianzen formen Beschließt das Apostelkonzil mit Mehrheit, die Gleichbere

In [12]:
for pattern, metric_list in all_metrics.items():
    print("Metrics for pattern " + str(pattern) + ":" + pattern_names[pattern])
    for metric in metric_list:
        print(metric.localizer_name)
        print("Tp: " + str(metric.tp))
        print("Fn: " + str(metric.fn))

        if(metric.hasNeg):
            print("Fp: " + str(metric.fp))
            print("Tn: " + str(metric.tn))

        print("Recall: " + str(metric.recall()))
        if(metric.hasNeg):
            print("Precision: " + str(metric.precision()))
            print("Accuracy: " + str(metric.accuracy()))
            print("F1: " + str(metric.F1()))
        else:
            print("No negative pattern sentences found!")
        print("")
    print("")
    print("####################################################################")
    print("")

Metrics for pattern 1292:Zufall
Matcher Lower
Tp: 0
Fn: 161
Fp: 0
Tn: 154
Recall: 0
Precision: 0
Accuracy: 0.4888888888888889
F1: 0

Matcher Lemma
Tp: 0
Fn: 161
Fp: 0
Tn: 154
Recall: 0
Precision: 0
Accuracy: 0.4888888888888889
F1: 0

Regex ohne Lemma
Tp: 152
Fn: 9
Fp: 17
Tn: 137
Recall: 0.9440993788819876
Precision: 0.8994082840236687
Accuracy: 0.9174603174603174
F1: 0.9212121212121213

Regex mit Lemma
Tp: 152
Fn: 9
Fp: 15
Tn: 139
Recall: 0.9440993788819876
Precision: 0.9101796407185628
Accuracy: 0.9238095238095239
F1: 0.926829268292683


####################################################################

Metrics for pattern 1409:Wählbarer Schwierigkeitsgrad
Matcher Lower
Tp: 0
Fn: 100
Recall: 0
No negative pattern sentences found!

Matcher Lemma
Tp: 0
Fn: 100
Recall: 0
No negative pattern sentences found!

Regex ohne Lemma
Tp: 0
Fn: 100
Recall: 0
No negative pattern sentences found!

Regex mit Lemma
Tp: 0
Fn: 100
Recall: 0
No negative pattern sentences found!


#####################

No negative pattern sentences found!


####################################################################

Metrics for pattern 5729:Erinnern
Matcher Lower
Tp: 0
Fn: 70
Recall: 0
No negative pattern sentences found!

Matcher Lemma
Tp: 0
Fn: 70
Recall: 0
No negative pattern sentences found!

Regex ohne Lemma
Tp: 0
Fn: 70
Recall: 0
No negative pattern sentences found!

Regex mit Lemma
Tp: 0
Fn: 70
Recall: 0
No negative pattern sentences found!


####################################################################

Metrics for pattern 5740:Joker
Matcher Lower
Tp: 0
Fn: 99
Recall: 0
No negative pattern sentences found!

Matcher Lemma
Tp: 0
Fn: 99
Recall: 0
No negative pattern sentences found!

Regex ohne Lemma
Tp: 0
Fn: 99
Recall: 0
No negative pattern sentences found!

Regex mit Lemma
Tp: 0
Fn: 99
Recall: 0
No negative pattern sentences found!


####################################################################

Metrics for pattern 7090:Kooperative Spielform
Matcher Lower
Tp: 0
Fn: 52


Regex mit Lemma
Tp: 0
Fn: 0
Recall: 0
No negative pattern sentences found!


####################################################################

Metrics for pattern 86801:Spielzugphase
Matcher Lower
Tp: 0
Fn: 18
Recall: 0
No negative pattern sentences found!

Matcher Lemma
Tp: 0
Fn: 18
Recall: 0
No negative pattern sentences found!

Regex ohne Lemma
Tp: 0
Fn: 18
Recall: 0
No negative pattern sentences found!

Regex mit Lemma
Tp: 0
Fn: 18
Recall: 0
No negative pattern sentences found!


####################################################################

Metrics for pattern 86813:Spielphase
Matcher Lower
Tp: 0
Fn: 197
Recall: 0
No negative pattern sentences found!

Matcher Lemma
Tp: 0
Fn: 197
Recall: 0
No negative pattern sentences found!

Regex ohne Lemma
Tp: 0
Fn: 197
Recall: 0
No negative pattern sentences found!

Regex mit Lemma
Tp: 0
Fn: 197
Recall: 0
No negative pattern sentences found!


####################################################################

Metrics for pattern 

In [13]:
for pattern, metric_list in all_metrics.items():
    print("Metrics for pattern " + str(pattern) + ":" + pattern_names[pattern])
    for metric in metric_list:
        if(metric.tp==0):
            continue
        print(metric.localizer_name)
        print("Tp: " + str(metric.tp))
        print("Fn: " + str(metric.fn))

        if(metric.hasNeg):
            print("Fp: " + str(metric.fp))
            print("Tn: " + str(metric.tn))

        print("Recall: " + str(metric.recall()))
        if(metric.hasNeg):
            print("Precision: " + str(metric.precision()))
            print("Accuracy: " + str(metric.accuracy()))
            print("F1: " + str(metric.F1()))
        else:
            print("No negative pattern sentences found!")
        print("")
    print("")
    print("####################################################################")
    print("")

Metrics for pattern 1292:Zufall
Regex ohne Lemma
Tp: 152
Fn: 9
Fp: 17
Tn: 137
Recall: 0.9440993788819876
Precision: 0.8994082840236687
Accuracy: 0.9174603174603174
F1: 0.9212121212121213

Regex mit Lemma
Tp: 152
Fn: 9
Fp: 15
Tn: 139
Recall: 0.9440993788819876
Precision: 0.9101796407185628
Accuracy: 0.9238095238095239
F1: 0.926829268292683


####################################################################

Metrics for pattern 1409:Wählbarer Schwierigkeitsgrad

####################################################################

Metrics for pattern 1417:Angemessener Schwierigkeitsgrad

####################################################################

Metrics for pattern 1433:Spielvarianten

####################################################################

Metrics for pattern 1446:Zeitlimit

####################################################################

Metrics for pattern 1455:Zug um Zug

####################################################################

Metrics fo

In [14]:
pattern_names

{1292: 'Zufall',
 1409: 'Wählbarer Schwierigkeitsgrad',
 1417: 'Angemessener Schwierigkeitsgrad',
 1433: 'Spielvarianten',
 1446: 'Zeitlimit',
 1455: 'Zug um Zug',
 1464: 'Informationsasymmetrie',
 1473: 'Spielendbedingung',
 1482: 'Sammeln',
 1492: 'Siegbedingung',
 1515: 'Ausholen',
 1665: 'Spielform',
 1756: 'Zwischenstand',
 2884: 'Tausch',
 2894: 'Ressourcen',
 2907: 'Veränderliches Spielfeld',
 2968: 'Ereignis',
 2981: 'Rolle',
 3085: 'Währung',
 3098: 'Belohnung',
 3142: 'Verlierbedingung',
 3173: 'Gemeinsames Spielfeld',
 3194: 'Avatar',
 3285: 'Feedback',
 3312: 'Punkte',
 3377: 'Aussetzen',
 3755: 'Unveränderliches Spielfeld',
 4426: 'Zugplanungserfordernis',
 5718: 'Gambling',
 5729: 'Erinnern',
 5740: 'Joker',
 7090: 'Kooperative Spielform',
 7098: 'Koordinierte Spielform',
 7106: 'Konfliktäre Spielform',
 7115: 'Kompetitive Spielform',
 7123: 'Team',
 7227: 'Negatives Ereignis',
 8520: 'Modifizierter Zufall',
 8528: 'Siegpunkte',
 8536: 'Aktionspunkte',
 8544: 'Handel',
 8

In [15]:
pattern = 1292
neg_file_name = validator_directory+"/"+str(pattern)+"-neg.txt"
with open(neg_file_name,"r") as f: 
    neg_sentences = f.readlines()
    neg_sentences = [x.strip() for x in neg_sentences]
    neg_sentences = " ".join(neg_sentences)
print(neg_sentences)

Für je 10 volle bekommt er 1 Siegpunkt der Rest verfällt. Die Spieler erhalten Zahlungen in Papiergeld die jeweils der Höhe des Gewinns der von ihnen kontrollierten Gesellschaften entsprechen. Wäre Lisa die letzte Spielerin gewesen die Grün kontrolliert hätte hätte sie den Kontrollstein behalten. Denn dann nimmt die Schlange eure Bewegungen wahr. Je der darf eine Strecke von nach bauen. Mit dem Kommando Angliedern 2 gliedert ein Regiment aus Korps seinem eigenen Korps an. Wenn der Angriff ein Scheinangriff war oder mit der Niederlage des Angreifers endete kann im Zug kein weiterer Angriff über diesen Zugang erfolgen. Der Gewinner der jeweils letzten Partie entscheidet ob er von links oder von rechts besetzen möchte. Der Spieler der an der Reihe ist hat jedesmal vier Punkte zur Verfügung. Die Büffel können nur geradeaus ziehen ein Feld pro Zug. Bei Gleichst für höchste Stufe 2 2 beteiligten Spieler Bonus. Aber wir haben auch nie behauptet daß die Landwirtschaft ein einfaches Gewerbe ist


print(client.get_pattern(183168))
pattern = 1473
print("patterns")
print(client.get_patterns())
print("")
print("negative patterns")
print(client.get_negative_patterns())
print("")
print("words for " + str(pattern))
print(client.get_pattern_evidence_words(pattern))
print("")
print("sentences for " + str(pattern))
print(client.get_pattern_evidence_sentences(pattern))

print("")
print("Random evidence pattern search")
print(client.evidence_pattern_search("","","1292",""))